In [1]:
import os
import random
import requests
import zipfile

from io import BytesIO

In [2]:
def download_and_extract_zip(url, extract_to="./"):
    try:
        print(f"Downloading dataset from {url}")
        response = requests.get(url)
        response.raise_for_status()

        with zipfile.ZipFile(BytesIO(response.content)) as z:
            print(f"Extracting files to '{extract_to}'...")
            z.extractall(extract_to)
            extracted_files = z.namelist()
            print(f"Extracted files: {extracted_files}")
    except Exception as e:
        print(f"An error occurred: {e}")

url = "https://coltekin.github.io/offensive-turkish/offenseval2020-turkish.zip"  # Replace with the actual URL
download_and_extract_zip(url, "./")

Extracting files to './'...
Extracted files: ['offenseval2020-turkish/', 'offenseval2020-turkish/offenseval-tr-training-v1/', 'offenseval2020-turkish/offenseval-tr-training-v1/offenseval-annotation.txt', 'offenseval2020-turkish/offenseval-tr-training-v1/offenseval-tr-training-v1.tsv', 'offenseval2020-turkish/offenseval-tr-training-v1/readme-trainingset-tr.txt', 'offenseval2020-turkish/offenseval-tr-testset-v1/', 'offenseval2020-turkish/offenseval-tr-testset-v1/offenseval-tr-testset-v1.tsv', 'offenseval2020-turkish/offenseval-tr-testset-v1/offenseval-tr-labela-v1.tsv', 'offenseval2020-turkish/README.txt']


In [3]:
original_train_file = "./offenseval2020-turkish/offenseval-tr-training-v1/offenseval-tr-training-v1.tsv"
original_test_file = "./offenseval2020-turkish/offenseval-tr-testset-v1/offenseval-tr-testset-v1.tsv"
orginal_label_test_file = "./offenseval2020-turkish/offenseval-tr-testset-v1/offenseval-tr-labela-v1.tsv"

In [4]:
def get_instances(filename: str):
    instances = []
    with open(filename, "rt") as f_p:
        for line in f_p:
            line = line.strip()
    
            if not line:
                continue
    
            if line.startswith("id"):
                continue
    
            _, tweet, label = line.split("\t")

            instances.append([label, tweet])

    print(f"Found {len(instances)} training instances.")

    return instances

In [5]:
def get_test_instances(filename: str, label_filename: str):
    # E.g. 41993,NOT is mapped to "41993" -> "NOT"
    id_label_mapping = {}
    with open(label_filename, "rt") as f_p:
        for line in f_p:
            line = line.strip()

            if not line:
                continue

            id_, label = line.split(",")

            id_label_mapping[id_] = label

    print(f"Found {len(id_label_mapping)} labelled test instances")

    instances = []
    
    with open(filename, "rt") as f_p:
        for line in f_p:
            line = line.strip()
    
            if not line:
                continue
    
            if line.startswith("id"):
                continue
    
            id_, tweet = line.split("\t")

            label = id_label_mapping[id_]

            instances.append([label, tweet])
    return instances

    assert len(id_label_mapping) == len(instances)

In [6]:
original_train_instances = get_instances(original_train_file)
original_test_instances = get_test_instances(original_test_file, orginal_label_test_file)

Found 31756 training instances.
Found 3528 labelled test instances


In [7]:
# Shuffling is done in-place
random.seed(83607)
random.shuffle(original_train_instances)

In [8]:
train_instances = original_train_instances[:30_000]
dev_instances = original_train_instances[30_000:]

In [9]:
def write_instances(instances: str, split_name: str):
    with open(f"{split_name}.txt", "wt") as f_out:
        for instance in instances:
            label, tweet = instance

            # We stick to Flair format for classification tasks, which is basically FastText inspired ;)
            new_label = "__label__" + label
            f_out.write(f"{new_label} {tweet}\n")

In [10]:
write_instances(train_instances, "train")
write_instances(dev_instances, "dev")
write_instances(original_test_instances, "test")